In [8]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [13]:
from kaggle_environments import make
import sys

## Test the agent loader

In [21]:
sys.path.append('/Users/jaime/Documents/MachineLearning/LuxAI/LuxAI-agents/')
from agent_loader import AgentLoader
from agents.rl_agents import RLAgent

In [22]:
agent = AgentLoader(agent_class=RLAgent).game_loop

In [23]:
# Test run in environment

env = make("lux_ai_2021", configuration={
#     "seed": 562124210, 
    "loglevel": 2, 
#     "annotations": True
}, debug=True)

steps = env.run([agent, "simple_agent"])
print(len(steps)-1)
env.render(mode="ipython", width=1200, height=800)

(24, 24, 14)
360


## Train agents

In [27]:
"""
sources:
    - https://github.com/Kaggle/kaggle-environments#training
    - https://github.com/Lux-AI-Challenge/Lux-Design-2021/blob/master/analysis/.ipynb_checkpoints/stepandreset-checkpoint.ipynb
    - https://www.kaggle.com/aithammadiabdellatif/keras-lux-ai-reinforcement-learning/comments
"""
from lux.game import Game

# Initialise training agent
myagent = RLAgent(team=0)

# Make environment (could choose configuration)
env = make("lux_ai_2021", debug=True)

# Training agent in first position (player 1) against "simple_agent"
trainer = env.train([None, "simple_agent"])
obs = trainer.reset()
game_state = Game()
game_state._initialize(obs["updates"])
game_state._update(obs["updates"][2:])
game_state.id = obs.player
eps = 1

max_steps = 1000
for turn in range(max_steps+1):

    # AGENT INTERACTION HERE
    # I guess reward shaping would happen inside get_actions
    actions = myagent.get_actions(game_state)
    
    obs, reward, done, info = trainer.step(actions)
    game_state._update(obs["updates"])
    
    if done:
        print(f'Episode {eps} complete.')
        print({"reward": reward,              # reward (final) is only given at the end of an episode (when "done")
               "obs_reward": obs["reward"],   # every observation (start of turn) also has an observation reward
               "obs_step": obs["step"]})      # print number of steps in this episode (to see if it made it to the end)
        
        # with open(f"replay-{eps}.json", "w") as f: # here we can save the replay as json for later
        #     f.write(env.render(mode="json"))
        
        # TODO: Perform parameter updates based on reward
        # reward_history = [ob['reward'] for ob in obs] # FIXME
        # reward_history.append(reward)  # Final reward
        # myagent.update_params(reward_history)
        
        # Re-init environment
        obs = trainer.reset()
        game_state = Game()
        game_state._initialize(obs["updates"])
        game_state._update(obs["updates"][2:])
        game_state.id = obs.player
        eps += 1
        
print(f'Episode {eps} complete.')
print({"reward": reward, 
       "obs_reward": obs["reward"],
       "obs_step": obs["step"]})
env.render(mode="ipython", width=1200, height=800)

(24, 24, 14)
Episode 1 complete.
{'reward': 0, 'obs_reward': 10001, 'obs_step': 360}
(24, 24, 14)
Episode 2 complete.
{'reward': 0, 'obs_reward': 10001, 'obs_step': 360}
(24, 24, 14)
Episode 3 complete.
{'reward': 0, 'obs_reward': 10001, 'obs_step': 281}
